In [129]:
from pandas import read_csv, to_datetime, DataFrame
from bokeh.models import ColumnDataSource, Span
from bokeh.plotting import figure, show
from bokeh.io import output_notebook
output_notebook()

from datetime import datetime,timedelta
from scipy import interpolate

Loading BokehJS ...

In [72]:
data = read_csv('method-failure-locations-rcp45.csv')
data.index.name = 'index'
data.columns = ['date',] + list(data.columns[1:]) 

data['date'] = to_datetime(data['date'] +'-01')


data_source =  ColumnDataSource(data)
data

date  St. Lawrence Is.  Outer Aleutians  Alaska Peninsula  \
index                                                                   
0     2006-01-01             -12.3             -1.5              -4.5   
1     2006-02-01             -13.3             -1.9              -2.7   
2     2006-03-01             -13.5             -0.2              -0.6   
3     2006-04-01              -9.0              1.5               1.5   
4     2006-05-01              -1.3              3.8               5.8   
...          ...               ...              ...               ...   
1135  2100-08-01              11.2             12.8              14.1   
1136  2100-09-01               8.3             11.7              11.8   
1137  2100-10-01               3.5              7.9               6.5   
1138  2100-11-01               0.5              4.4               2.6   
1139  2100-12-01              -0.1              2.4               1.1   

       Chugach National Forest  South East Ak  Canada  
index                                                  
0                         -2.6            0.1     6.1  
1                         -0.8            2.0     6.6  
2                          0.6            2.7     8.2  
3                          3.4            4.5     9.5  
4                          7.5            7.6    12.0  
...                        ...            ...     ...  
1135                      14.3           15.9    21.2  
1136                      11.3           12.8    18.2  
1137                       7.6            9.3    12.8  
1138                       0.7            4.2     9.2  
1139                      -0.3            2.7     6.3  

[1140 rows x 7 columns]

In [144]:

for location in list(data.columns[1:]) :
#     location = 'St. Lawrence Is.'
    fig = figure(
        sizing_mode="stretch_width", height=200,
        x_axis_type='datetime',
    #     tools="pan,box_zoom,reset,save",
        tools='xpan,box_zoom,xwheel_pan,xwheel_zoom,reset,save', 
        active_scroll='xwheel_pan',
        x_range=(datetime(2006,1,1), datetime(2011,1,1)),
        y_range=(-30, 30),
        x_axis_label='Date',
        y_axis_label='Degrees Celsius'
    )

    day_array = (data['date'] - data['date'][0]).apply(lambda x: x.days)
    spline = interpolate.UnivariateSpline(
        day_array.values, data[location].values
    )
    spline_table = DataFrame({'date':range(0,day_array.values[-1])})
    # spline_table['spline(x)'] = 0
    spline_table['spline(x)'] = spline_table['date'].apply(
        lambda x: spline(x)
    )
    spline_table['date'] = spline_table['date'].apply(
        lambda x: data['date'][0] + timedelta(days=x)
    )
    spline_source = ColumnDataSource(spline_table)

    hline = Span(
        location=0,dimension='width', 
        line_color='red',line_width=1
    )
    fig.renderers.extend([hline])
    fig.scatter(
        x = 'date', y = location, source = data_source,
        line_width=3, line_alpha=0.6
    )
    fig.line(
        x = 'date', y = 'spline(x)', source = spline_source,
        line_width=1, line_alpha=0.6 , color = 'green'
    )
    fig.title = 'Monthly Temperature for %s -> N roots: %s' % \
        (location,len(spline.roots()))


    show(fig)

In [131]:
spline_table

date  spline(x)
0     2006-01-01 -11.378629
1     2006-01-02 -11.378629
2     2006-01-03 -11.378629
3     2006-01-04 -11.378629
4     2006-01-05 -11.378629
...          ...        ...
34662 2100-11-26 -11.378629
34663 2100-11-27 -11.378629
34664 2100-11-28 -11.378629
34665 2100-11-29 -11.378629
34666 2100-11-30 -11.378629

[34667 rows x 2 columns]

192